In [1]:
from langchain_community.document_loaders.csv_loader import CSVLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
import pandas as pd
import langchain
import os
import openai
import ast
from langchain import OpenAI
from langchain.chains.qa_with_sources.loading import load_qa_with_sources_chain
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.document_loaders import UnstructuredURLLoader
from langchain.embeddings import OpenAIEmbeddings
from langchain.vectorstores import FAISS

In [9]:
# loader = CSVLoader(file_path="trials/brief_summaries.csv")
# data = loader.load()

In [10]:
# df= pd.read_csv("trials/brief_summaries.txt",  delimiter="|")
# df.shape

In [11]:
# df.head(20)

In [2]:
os.environ['OPENAI_API_KEY']="sk-proj-CG2E98bSWs53X2eWO0Z4T3BlbkFJLm7H1vfkbua0zP548CKQ"

In [3]:
llm= OpenAI(
    temperature=0.6, max_tokens=500
)

/Users/aldan.creo/miniconda3/envs/hackupc/lib/python3.11/site-packages/langchain_core/_api/deprecation.py:119: LangChainDeprecationWarning: The class `OpenAI` was deprecated in LangChain 0.0.10 and will be removed in 0.2.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import OpenAI`.
  warn_deprecated(


In [14]:
df_trials= pd.read_csv("clinical_trials.csv")
print(df_trials.shape)
df_trials.head()

(440517, 2)


desease_condition  \
0  ['marijuana abuse', 'substance-related disorde...   
1  ['marijuana abuse', 'substance-related disorde...   
2  ['tuberculosis', 'latent tuberculosis', 'infec...   
3  ['heart failure', 'heart diseases', 'cardiovas...   
4  ['lymphoma', 'neoplasms by histologic type', '...   

                                                text  
0  nct_id: NCT03055377\nsummary: This is a 12-wee...  
1  nct_id: NCT03055377\nsummary: This is a 12-wee...  
2  nct_id: NCT03042754\nsummary: Early diagnosis ...  
3  nct_id: NCT03035123\nsummary: The EduStra-HF s...  
4  nct_id: NCT02272751\nsummary: This study will ...

In [15]:
df_trials_filtered=df_trials[['desease_condition']]
df_trials_filtered.head()

desease_condition
0  ['marijuana abuse', 'substance-related disorde...
1  ['marijuana abuse', 'substance-related disorde...
2  ['tuberculosis', 'latent tuberculosis', 'infec...
3  ['heart failure', 'heart diseases', 'cardiovas...
4  ['lymphoma', 'neoplasms by histologic type', '...

In [16]:
df_trials_filtered['desease_condition'].iloc[0]

"['marijuana abuse', 'substance-related disorders', 'chemically-induced disorders', 'mental disorders']"

In [17]:
def list_to_string(disease_list):
    disease_list= ast.literal_eval(disease_list)
    return ', '.join(disease_list)
df_trials_filtered['desease_condition']= df_trials_filtered['desease_condition'].apply(list_to_string)
df_trials_filtered

C:\Users\ariji\AppData\Local\Temp\ipykernel_22340\16068817.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_trials_filtered['desease_condition']= df_trials_filtered['desease_condition'].apply(list_to_string)


desease_condition
0       marijuana abuse, substance-related disorders, ...
1       marijuana abuse, substance-related disorders, ...
2       tuberculosis, latent tuberculosis, infections,...
3       heart failure, heart diseases, cardiovascular ...
4       lymphoma, neoplasms by histologic type, neopla...
...                                                   ...
440512  obesity, overweight, overnutrition, nutrition ...
440513  obesity, overweight, overnutrition, nutrition ...
440514  obesity, overweight, overnutrition, nutrition ...
440515  autistic disorder, autism spectrum disorder, c...
440516  autistic disorder, autism spectrum disorder, c...

[440517 rows x 1 columns]

In [18]:
df_trials_filtered['desease_condition'].head()

0    marijuana abuse, substance-related disorders, ...
1    marijuana abuse, substance-related disorders, ...
2    tuberculosis, latent tuberculosis, infections,...
3    heart failure, heart diseases, cardiovascular ...
4    lymphoma, neoplasms by histologic type, neopla...
Name: desease_condition, dtype: object

In [19]:
df_trials_filtered.to_csv("diseases.csv", index=False)

In [20]:
loader= CSVLoader(file_path="./diseases.csv", encoding="utf-8")
data = loader.load()
len(data)

440517

In [ ]:
embeddings = OpenAIEmbeddings()
vectorstore = FAISS.from_documents(data, embeddings)

In [ ]:
file_path= "vector_index.pkl"
with open(file_path, "wb") as f:
    pickle.dump(vectorstore, f)

In [98]:
df_trials= pd.read_csv("clinical_trials.csv")
print(df_trials.shape)
df_trials.head()

(440517, 2)


desease_condition  \
0  ['marijuana abuse', 'substance-related disorde...   
1  ['marijuana abuse', 'substance-related disorde...   
2  ['tuberculosis', 'latent tuberculosis', 'infec...   
3  ['heart failure', 'heart diseases', 'cardiovas...   
4  ['lymphoma', 'neoplasms by histologic type', '...   

                                                text  
0  nct_id: NCT03055377\nsummary: This is a 12-wee...  
1  nct_id: NCT03055377\nsummary: This is a 12-wee...  
2  nct_id: NCT03042754\nsummary: Early diagnosis ...  
3  nct_id: NCT03035123\nsummary: The EduStra-HF s...  
4  nct_id: NCT02272751\nsummary: This study will ...

In [99]:
df_trials.iloc[0].text

"nct_id: NCT03055377\nsummary: This is a 12-week randomized, placebo-controlled trial of N-acetylcysteine for cannabis use disorder (CUD) in youth (N=192). Participants will be randomized to double-blind NAC or PBO, yielding two equally-allocated treatment groups. All participants will receive brief weekly cannabis cessation counseling and medication management. The primary efficacy outcome will be the proportion of negative urine cannabinoid tests during the 12-week active treatment, compared between groups.\nintervention_type: Drug\nintervention_name: N-acetyl cysteine\nintervention_description: N-acetylcysteine 1200 mg twice daily for 12 weeks (administered orally)\nkeywords: ['cannabis', 'marijuana', 'youth', 'adolescent', 'pharmacotherapy', 'medication', 'n-acetylcysteine', 'trial']"

In [100]:
df= df_trials[:1000]
df.shape

(1000, 2)

In [ ]:
embeddings= OpenAIEmbeddings()
vectorindex_openapi= FAISS.from

In [6]:
df_trials_filtered = pd.read_csv("diseases.csv")
df_trials_filtered

desease_condition
0       marijuana abuse, substance-related disorders, ...
1       marijuana abuse, substance-related disorders, ...
2       tuberculosis, latent tuberculosis, infections,...
3       heart failure, heart diseases, cardiovascular ...
4       lymphoma, neoplasms by histologic type, neopla...
...                                                   ...
440512  obesity, overweight, overnutrition, nutrition ...
440513  obesity, overweight, overnutrition, nutrition ...
440514  obesity, overweight, overnutrition, nutrition ...
440515  autistic disorder, autism spectrum disorder, c...
440516  autistic disorder, autism spectrum disorder, c...

[440517 rows x 1 columns]

In [49]:
df2= df_trials_filtered[:100]
df2.shape

(100, 1)

In [7]:
from openai import OpenAI
client= OpenAI()

In [8]:
def get_embeddings(text):
    response= client.embeddings.create(
        input= text,
        dimensions= 128,
        model= "text-embedding-3-small"
    )
    return response.data[0].embedding

In [9]:
%%time
from  sentence_transformers import SentenceTransformer

encoder= SentenceTransformer("all-mpnet-base-v2")
vectors= encoder.encode(df2.desease_condition)
vectors.shape

ModuleNotFoundError: No module named 'sentence_transformers'

In [66]:
%%time
df2['embeddings']= df2['desease_condition'].apply(get_embeddings)
df2.head()

CPU times: total: 62.5 ms
Wall time: 24.7 s


<timed exec>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


desease_condition  \
0  marijuana abuse, substance-related disorders, ...   
1  marijuana abuse, substance-related disorders, ...   
2  tuberculosis, latent tuberculosis, infections,...   
3  heart failure, heart diseases, cardiovascular ...   
4  lymphoma, neoplasms by histologic type, neopla...   

                                          embeddings  
0  [-0.05811865255236626, -0.023393018171191216, ...  
1  [-0.05811865255236626, -0.023393018171191216, ...  
2  [-0.03460180386900902, -0.084668830037117, 0.2...  
3  [-0.08236236125230789, -0.1235777735710144, 0....  
4  [-0.1227850392460823, 0.07155642658472061, 0.1...

In [65]:
import numpy as np
np.array(df2.iloc[0].embeddings).shape

(128,)

In [23]:
from  sentence_transformers import SentenceTransformer

encoder= SentenceTransformer("all-mpnet-base-v2")
vectors= encoder.encode(df2.desease_condition)
vectors.shape

C:\Users\ariji\Anaconda3\envs\python310\lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


KeyboardInterrupt: 

In [102]:
print(vectors)

[[ 0.01245328  0.07695839  0.01802037 ...  0.0093326  -0.03474615
  -0.02757339]
 [ 0.01846956  0.08282936  0.01921537 ...  0.01068991 -0.03402989
  -0.02075185]
 [ 0.01822413 -0.05593034 -0.00288358 ...  0.03525289 -0.05427228
  -0.03371295]
 ...
 [ 0.04031958  0.0040107   0.02156032 ...  0.01568209 -0.04320977
  -0.02990234]
 [ 0.0399131   0.00027251  0.02207735 ...  0.01440835 -0.04246744
  -0.02869584]
 [ 0.03773859 -0.00315346  0.0207725  ...  0.01205995 -0.04628598
  -0.02870333]]


In [103]:
dim= vectors.shape[1]
dim 

768

In [106]:
import faiss

index= faiss.IndexFlatL2(dim)
index

<faiss.swigfaiss_avx2.IndexFlatL2; proxy of <Swig Object of type 'faiss::IndexFlatL2 *' at 0x0000023493347480> >

In [107]:
index.add(vectors)

In [108]:
search_query= "clinical trials related to alzheimers"
vec= encoder.encode(search_query)
print(vec.shape)
vec

(768,)


array([-8.82369652e-03,  8.50650743e-02,  2.08267733e-03,  6.77651772e-03,
       -2.86661759e-02, -8.71188380e-03,  6.99447095e-02,  5.04214764e-02,
        3.58386151e-02,  5.29594952e-03, -1.40875215e-02,  1.99297220e-02,
        2.27009598e-03,  2.10810862e-02,  2.66138893e-02,  1.90623086e-02,
        4.44708914e-02,  2.96202525e-02,  5.42085357e-02, -2.34859088e-03,
       -9.87798795e-02, -5.00183590e-02, -3.42465192e-02,  2.08440255e-02,
        5.31156994e-02, -1.37044629e-02,  2.92537250e-02, -2.61334293e-02,
       -1.21854078e-04, -2.36813519e-02, -3.81283499e-02, -1.79494768e-02,
       -6.29265187e-03,  1.27150817e-02,  1.19849676e-06, -7.78729608e-03,
       -1.28973828e-04,  4.01791967e-02,  4.21229303e-02, -8.72302521e-03,
        7.44823692e-03,  7.68032745e-02,  6.50246907e-03,  3.40298638e-02,
       -1.80711355e-02, -2.71878559e-02,  5.74751608e-02,  3.67745496e-02,
       -3.34868580e-02,  1.05205458e-02,  2.08975170e-02,  4.36686277e-02,
        3.47612537e-02, -

In [109]:
import numpy as np
svec= np.array(vec).reshape(1,-1)
print(svec.shape)
svec

(1, 768)


array([[-8.82369652e-03,  8.50650743e-02,  2.08267733e-03,
         6.77651772e-03, -2.86661759e-02, -8.71188380e-03,
         6.99447095e-02,  5.04214764e-02,  3.58386151e-02,
         5.29594952e-03, -1.40875215e-02,  1.99297220e-02,
         2.27009598e-03,  2.10810862e-02,  2.66138893e-02,
         1.90623086e-02,  4.44708914e-02,  2.96202525e-02,
         5.42085357e-02, -2.34859088e-03, -9.87798795e-02,
        -5.00183590e-02, -3.42465192e-02,  2.08440255e-02,
         5.31156994e-02, -1.37044629e-02,  2.92537250e-02,
        -2.61334293e-02, -1.21854078e-04, -2.36813519e-02,
        -3.81283499e-02, -1.79494768e-02, -6.29265187e-03,
         1.27150817e-02,  1.19849676e-06, -7.78729608e-03,
        -1.28973828e-04,  4.01791967e-02,  4.21229303e-02,
        -8.72302521e-03,  7.44823692e-03,  7.68032745e-02,
         6.50246907e-03,  3.40298638e-02, -1.80711355e-02,
        -2.71878559e-02,  5.74751608e-02,  3.67745496e-02,
        -3.34868580e-02,  1.05205458e-02,  2.08975170e-0

In [110]:
distances, I= index.search(svec, k=2)
print(distances, I)

[[0.7731663  0.79433584]] [[330 331]]


In [111]:
df2= df.iloc[I[0]]
df2

desease_condition  \
330  ['alzheimer disease', 'dementia', 'brain disea...   
331  ['alzheimer disease', 'dementia', 'brain disea...   

                                                  text  
330  nct_id: NCT02164643\nsummary: A Multicenter na...  
331  nct_id: NCT02164643\nsummary: A Multicenter na...

In [113]:
df2.iloc[1].text

'nct_id: NCT02164643\nsummary: A Multicenter national longitudinal cohort study including at least 800 individuals consecutively recruited from French Research Memory Centers and followed-up over 24 month and included in Memento.\nintervention_type: Drug\nintervention_name: Florbetapir (18F)\nintervention_description: nan\nkeywords: ["Alzheimer\'s disease", \'Mild Cognitive Impairment\']'